1. Set x1 and x2 distribution.
    - x1 = Gaussian, mean = 0, standard deviation = 1
    - x2 = Gaussian, mean = 5, standard deviatibn = 2
2. Generate x1 and x2 based on distribution
    - Both 100 data

Multi label classification

In [1]:
import numpy as np
import random
import sys

from keras.datasets import mnist
from keras.layers import Activation, BatchNormalization
from keras.layers import Conv2D, MaxPooling2D
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers.advanced_activations import LeakyReLU
from keras.models import Sequential, Model
from keras.models import load_model
from keras.optimizers import Adam
from keras.utils import to_categorical

Using TensorFlow backend.


In [2]:
class GAN():
    
    def __init__(self):
        self.data_shape = (2,)
        self.noise_shape = (10,)

        # Manually tune down learning rate to avoid oscillation
        optimizer = Adam(lr=0.0002, beta_1=0.5)

        # -------------
        # Discriminator
        # -------------
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='mean_squared_error',
                                   optimizer=optimizer,
                                   metrics=['accuracy'])
        # ---------
        # Generator
        # ---------
        self.generator = self.build_generator()
        self.generator.compile(loss='mean_squared_error',
                               optimizer=optimizer)
        # --------
        # Combined
        # --------
        # The combined model is created by stacking generator and discriminator.
        # Noise ---Generator--> Generated Image ---Discriminator--> Validity
        
        z = Input(shape=self.noise_shape)
        data = self.generator(z)

        # For the combined model we will only train the generator
        self.discriminator.trainable = False
        
        validity = self.discriminator(data)

        self.combined = Model(z, validity)
        self.combined.compile(loss='mean_squared_error',
                              optimizer=optimizer)

        
    def save_model(self, version=None):
        if version is None:
            self.discriminator.save('gan/models/toy-discriminator.h5')
            self.generator.save('gan/models/toy-generator.h5')
            self.combined.save('gan/models/toy-combined.h5')
        else:
            self.discriminator.save('gan/models/toy-discriminator-{}.h5'.format(version))
            self.generator.save('gan/models/toy-generator-{}.h5'.format(version))
            self.combined.save('gan/models/toy-combined-{}.h5'.format(version))
        
        
    def load_model(self, version=None): 
        if version is None:
            self.discriminator = load_model('gan/models/toy-discriminator.h5')
            self.generator = load_model('gan/models/toy-generator.h5')
            self.combined = load_model('gan/models/toy-combined.h5')
        else:
            self.discriminator = load_model('gan/models/toy-discriminator-{}.h5'.format(version))
            self.generator = load_model('gan/models/toy-generator-{}.h5'.format(version))
            self.combined = load_model('gan/models/toy-combined-{}.h5'.format(version))
            
        
    def build_discriminator(self):
        model = Sequential()
        model.add(Dense(4, input_shape=self.data_shape))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(8))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1, activation='sigmoid'))
        
        model.summary()

        # Discriminator takes an image as an input and outputs its validity
        data = Input(shape=self.data_shape)
        validity = model(data)

        return Model(data, validity)

        
    def build_generator(self):
        # BatchNormalization maintains the mean activation close to 0
        # and the activation standard deviation close to 1
        model = Sequential()
        model.add(Dense(8, input_shape=self.noise_shape))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(4))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(2))
        
        model.summary()

        # Generator takes noise as an input and outputs an image
        noise = Input(shape=self.noise_shape)
        data = model(noise)

        return Model(noise, data)
    
    
    def train(self, x_train, epochs, batch_size=128, save_model_interval=5000):

        half_batch = int(batch_size / 2)
        
        for epoch in range(epochs):
            # -------------------
            # Train Discriminator
            # -------------------
            # Select a random half batch of images
            idx = np.random.randint(0, x_train.shape[0], half_batch)
            data = x_train[idx]

            # Generate a half batch of new images
            noise = np.random.normal(0, 1, (half_batch, 10))
            gen_data = self.generator.predict(noise)

            # Train the discriminator
            d_loss_real = self.discriminator.train_on_batch(data, np.ones((half_batch, 1)))
            d_loss_fake = self.discriminator.train_on_batch(gen_data, np.zeros((half_batch, 1)))
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

            # ---------------
            # Train Generator
            # ---------------
            noise = np.random.normal(0, 1, (batch_size, 10))

            # The generator wants to fool the discriminator, hence trained with valid label (1)
            # valid_y = np.array([1] * batch_size)
            valid_y = np.ones((batch_size, 1))

            # Train the generator
            g_loss = self.combined.train_on_batch(noise, valid_y)


            # Print progress
            print ("{:5d} [D loss: {}, acc_real: {:2f}, acc_fake: {:2f}] [G loss: {}]".format(epoch, d_loss[0], 100*d_loss_real[1], 100*d_loss_fake[1], g_loss))

            with open('gan/logs/toy-gan.log', 'a') as log_file:
                log_file.write('{},{}\n'.format(d_loss[0], g_loss))
            
            
            # Save models at save_interval
            if epoch != 0 and epoch % save_model_interval == 0:
                self.save_model(version=str(epoch))
                

if __name__ == '__main__':
    mu_x1 = 0
    sd_x1 = 1

    x1 = np.random.normal(mu_x1, sd_x1, 10000)

    print(np.mean(x1))
    print(np.std(x1))

    mu_x2 = 5
    sd_x2 = 2

    x2 = np.random.normal(mu_x2, sd_x2, 10000)

    print(np.mean(x2))
    print(np.std(x2))
    
    x_train = np.stack((x1, x2))
    x_train = np.transpose(x_train)
    print(x_train.shape)
    
    gan = GAN()
    gan.train(x_train, epochs=50001, batch_size=128, save_model_interval=10000)

-0.009685816147027348
1.006323158755088
4.959157151631162
1.9935936701464454
(10000, 2)
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 4)                 12        
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 4)                 0         
_________________________________________________________________
dense_2 (Dense)              (None, 8)                 40        
_________________________________________________________________
leaky_re_lu_2 (LeakyReLU)    (None, 8)                 0         
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 9         
Total params: 61
Trainable params: 61
Non-trainable params: 0
_________________________________________________________________
__________________________________________________________

/home/rionaldichandraseta/miniconda3/envs/gan-image/lib/python3.6/site-packages/keras/engine/training.py:478: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


    0 [D loss: 0.26285320520401, acc_real: 3.125000, acc_fake: 68.750000] [G loss: 0.33741816878318787]
    1 [D loss: 0.25864702463150024, acc_real: 0.000000, acc_fake: 62.500000] [G loss: 0.3409138321876526]
    2 [D loss: 0.2549528479576111, acc_real: 0.000000, acc_fake: 56.250000] [G loss: 0.33153361082077026]
    3 [D loss: 0.24315860867500305, acc_real: 3.125000, acc_fake: 65.625000] [G loss: 0.33238232135772705]
    4 [D loss: 0.24490894377231598, acc_real: 0.000000, acc_fake: 57.812500] [G loss: 0.3295803368091583]
    5 [D loss: 0.25900301337242126, acc_real: 3.125000, acc_fake: 56.250000] [G loss: 0.33541032671928406]
    6 [D loss: 0.25185126066207886, acc_real: 0.000000, acc_fake: 65.625000] [G loss: 0.3350052833557129]
    7 [D loss: 0.2425546497106552, acc_real: 3.125000, acc_fake: 60.937500] [G loss: 0.33402562141418457]
    8 [D loss: 0.25576281547546387, acc_real: 3.125000, acc_fake: 53.125000] [G loss: 0.32963722944259644]
    9 [D loss: 0.24123413860797882, acc_real:

   87 [D loss: 0.21140669286251068, acc_real: 96.875000, acc_fake: 45.312500] [G loss: 0.32034990191459656]
   88 [D loss: 0.20615097880363464, acc_real: 95.312500, acc_fake: 48.437500] [G loss: 0.3173289895057678]
   89 [D loss: 0.20184141397476196, acc_real: 95.312500, acc_fake: 45.312500] [G loss: 0.3274027705192566]
   90 [D loss: 0.20818543434143066, acc_real: 93.750000, acc_fake: 42.187500] [G loss: 0.3236987590789795]
   91 [D loss: 0.20256419479846954, acc_real: 96.875000, acc_fake: 48.437500] [G loss: 0.3159554898738861]
   92 [D loss: 0.19959339499473572, acc_real: 93.750000, acc_fake: 56.250000] [G loss: 0.31683388352394104]
   93 [D loss: 0.20384393632411957, acc_real: 100.000000, acc_fake: 45.312500] [G loss: 0.32440119981765747]
   94 [D loss: 0.20597051084041595, acc_real: 96.875000, acc_fake: 43.750000] [G loss: 0.31873518228530884]
   95 [D loss: 0.2108336240053177, acc_real: 98.437500, acc_fake: 42.187500] [G loss: 0.3175122141838074]
   96 [D loss: 0.1952466964721679

  168 [D loss: 0.18225201964378357, acc_real: 95.312500, acc_fake: 40.625000] [G loss: 0.31573933362960815]
  169 [D loss: 0.164546936750412, acc_real: 98.437500, acc_fake: 51.562500] [G loss: 0.30958059430122375]
  170 [D loss: 0.17357860505580902, acc_real: 100.000000, acc_fake: 48.437500] [G loss: 0.30984973907470703]
  171 [D loss: 0.1803818643093109, acc_real: 98.437500, acc_fake: 32.812500] [G loss: 0.30477505922317505]
  172 [D loss: 0.19085349142551422, acc_real: 95.312500, acc_fake: 40.625000] [G loss: 0.3032803535461426]
  173 [D loss: 0.18509195744991302, acc_real: 93.750000, acc_fake: 42.187500] [G loss: 0.3029516041278839]
  174 [D loss: 0.18018876016139984, acc_real: 95.312500, acc_fake: 45.312500] [G loss: 0.3086492419242859]
  175 [D loss: 0.1825142204761505, acc_real: 98.437500, acc_fake: 35.937500] [G loss: 0.30547288060188293]
  176 [D loss: 0.17661195993423462, acc_real: 96.875000, acc_fake: 46.875000] [G loss: 0.3056533634662628]
  177 [D loss: 0.17391937971115112,

...

49622 [D loss: 0.2501488924026489, acc_real: 64.062500, acc_fake: 31.250000] [G loss: 0.2498319149017334]
49623 [D loss: 0.25010642409324646, acc_real: 70.312500, acc_fake: 20.312500] [G loss: 0.24978208541870117]
49624 [D loss: 0.2503182291984558, acc_real: 57.812500, acc_fake: 17.187500] [G loss: 0.249728262424469]
49625 [D loss: 0.2502188980579376, acc_real: 70.312500, acc_fake: 17.187500] [G loss: 0.2497156858444214]
49626 [D loss: 0.25016599893569946, acc_real: 65.625000, acc_fake: 12.500000] [G loss: 0.24961863458156586]
49627 [D loss: 0.24989324808120728, acc_real: 79.687500, acc_fake: 20.312500] [G loss: 0.24952462315559387]
49628 [D loss: 0.25054246187210083, acc_real: 56.250000, acc_fake: 15.625000] [G loss: 0.24964562058448792]
49629 [D loss: 0.25023379921913147, acc_real: 64.062500, acc_fake: 34.375000] [G loss: 0.2497062385082245]
49630 [D loss: 0.2501031756401062, acc_real: 65.625000, acc_fake: 26.562500] [G loss: 0.24973420798778534]
49631 [D loss: 0.25005602836608887, a

49710 [D loss: 0.25031399726867676, acc_real: 1.562500, acc_fake: 98.437500] [G loss: 0.25127729773521423]
49711 [D loss: 0.25026223063468933, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.2513195276260376]
49712 [D loss: 0.25005191564559937, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.25137758255004883]
49713 [D loss: 0.2504499554634094, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.25139886140823364]
49714 [D loss: 0.25023525953292847, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.2514423131942749]
49715 [D loss: 0.25030210614204407, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.25147193670272827]
49716 [D loss: 0.2502879202365875, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.2514883875846863]
49717 [D loss: 0.2503221929073334, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.25145307183265686]
49718 [D loss: 0.250299870967865, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.2514907419681549]
49719 [D loss: 0.25023287534713745, ac

49799 [D loss: 0.2502727508544922, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.252469927072525]
49800 [D loss: 0.2502220869064331, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.25245898962020874]
49801 [D loss: 0.2501777410507202, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.2524923086166382]
49802 [D loss: 0.2501806616783142, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.2525092363357544]
49803 [D loss: 0.250344455242157, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.25246405601501465]
49804 [D loss: 0.2500936985015869, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.252471923828125]
49805 [D loss: 0.25013092160224915, acc_real: 0.000000, acc_fake: 100.000000] [G loss: 0.2524970769882202]
49806 [D loss: 0.2501523494720459, acc_real: 1.562500, acc_fake: 100.000000] [G loss: 0.2525111436843872]
49807 [D loss: 0.25006118416786194, acc_real: 3.125000, acc_fake: 100.000000] [G loss: 0.25249001383781433]
49808 [D loss: 0.25020116567611694, acc_real

49886 [D loss: 0.2501378059387207, acc_real: 21.875000, acc_fake: 42.187500] [G loss: 0.25015023350715637]
49887 [D loss: 0.25027385354042053, acc_real: 35.937500, acc_fake: 23.437500] [G loss: 0.24997952580451965]
49888 [D loss: 0.2502295970916748, acc_real: 51.562500, acc_fake: 10.937500] [G loss: 0.24986249208450317]
49889 [D loss: 0.2503524422645569, acc_real: 62.500000, acc_fake: 4.687500] [G loss: 0.24977639317512512]
49890 [D loss: 0.2501766085624695, acc_real: 71.875000, acc_fake: 3.125000] [G loss: 0.2496945858001709]
49891 [D loss: 0.25022652745246887, acc_real: 62.500000, acc_fake: 0.000000] [G loss: 0.24965214729309082]
49892 [D loss: 0.25020360946655273, acc_real: 75.000000, acc_fake: 0.000000] [G loss: 0.24953773617744446]
49893 [D loss: 0.2502468228340149, acc_real: 89.062500, acc_fake: 0.000000] [G loss: 0.24943384528160095]
49894 [D loss: 0.2502082586288452, acc_real: 81.250000, acc_fake: 0.000000] [G loss: 0.24936166405677795]
49895 [D loss: 0.2505998909473419, acc_re

49978 [D loss: 0.24986958503723145, acc_real: 90.625000, acc_fake: 3.125000] [G loss: 0.24930331110954285]
49979 [D loss: 0.25025975704193115, acc_real: 78.125000, acc_fake: 0.000000] [G loss: 0.24927407503128052]
49980 [D loss: 0.25036025047302246, acc_real: 78.125000, acc_fake: 0.000000] [G loss: 0.24925827980041504]
49981 [D loss: 0.25033068656921387, acc_real: 82.812500, acc_fake: 1.562500] [G loss: 0.24933236837387085]
49982 [D loss: 0.24996954202651978, acc_real: 84.375000, acc_fake: 0.000000] [G loss: 0.2494894564151764]
49983 [D loss: 0.250282883644104, acc_real: 78.125000, acc_fake: 0.000000] [G loss: 0.24952432513237]
49984 [D loss: 0.24990083277225494, acc_real: 71.875000, acc_fake: 1.562500] [G loss: 0.2496308982372284]
49985 [D loss: 0.2502075731754303, acc_real: 70.312500, acc_fake: 3.125000] [G loss: 0.24969644844532013]
49986 [D loss: 0.2502816915512085, acc_real: 71.875000, acc_fake: 7.812500] [G loss: 0.24978254735469818]
49987 [D loss: 0.25026029348373413, acc_real: 

In [5]:
gan = GAN()
gan.load_model(version='40000')

noise = np.random.normal(0, 1, (1000, 10))
new_x = gan.generator.predict(noise)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_13 (Dense)             (None, 4)                 12        
_________________________________________________________________
leaky_re_lu_9 (LeakyReLU)    (None, 4)                 0         
_________________________________________________________________
dense_14 (Dense)             (None, 8)                 40        
_________________________________________________________________
leaky_re_lu_10 (LeakyReLU)   (None, 8)                 0         
_________________________________________________________________
dense_15 (Dense)             (None, 1)                 9         
Total params: 61
Trainable params: 61
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_16 (Dens

/home/rionaldichandraseta/miniconda3/envs/gan-image/lib/python3.6/site-packages/keras/engine/saving.py:305: UserWarning: Error in loading the saved optimizer state. As a result, your model is starting with a freshly initialized optimizer.
  warnings.warn('Error in loading the saved optimizer '


In [6]:
new_x1 = []
new_x2 = []

for xs in new_x:
    new_x1.append(xs[0])
    new_x2.append(xs[1])
    
print(np.mean(new_x1))
print(np.std(new_x1))

print(np.mean(new_x2))
print(np.std(new_x2))

0.08895265
0.9411747
4.7931485
2.0114353
